In [ ]:
!pip install -U -q "google-genai>=1.16.1"

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 223.8/223.8 kB 14.0 MB/s eta 0:00:00


# Gemini TTS


### Setup your API key for Using AIStudio


In [ ]:
from google.colab import userdata

GOOGLE_API_KEY= ""
import os
os.environ['GOOGLE_API_KEY'] = ""

### Initialize SDK client


In [ ]:
from google import genai
from google.genai import types

client = genai.Client(
    api_key=GOOGLE_API_KEY,
    )

### Initialize SDK client


In [ ]:
from google import genai
from google.genai import types
from google.genai.types import GenerateContentConfig, Tool
from IPython.display import display, HTML, Markdown
import io
import json
import re

### Getting a list of models

In [ ]:
for model in client.models.list(config={'query_base':True}):
    if 'tts' in model.name:
        print(model)

name='models/gemini-2.5-flash-preview-tts' display_name='Gemini 2.5 Flash Preview TTS' description='Gemini 2.5 Flash Preview TTS' version='gemini-2.5-flash-exp-tts-2025-05-19' endpoints=None labels=None tuned_model_info=TunedModelInfo() input_token_limit=8192 output_token_limit=16384 supported_actions=['countTokens', 'generateContent'] default_checkpoint_id=None checkpoints=None
name='models/gemini-2.5-pro-preview-tts' display_name='Gemini 2.5 Pro Preview TTS' description='Gemini 2.5 Pro Preview TTS' version='gemini-2.5-pro-preview-tts-2025-05-19' endpoints=None labels=None tuned_model_info=TunedModelInfo() input_token_limit=8192 output_token_limit=16384 supported_actions=['countTokens', 'generateContent'] default_checkpoint_id=None checkpoints=None


## Basic TTS - Single Voice

In [ ]:
from google import genai
from google.genai import types
import wave
import os
import base64
import struct


from IPython.display import Audio, display

In [ ]:
# Set up the wave file to save the output:
def wave_file(filename, pcm, channels=1, rate=24000, sample_width=2):
   print(f"\nWriting audio file with parameters:")
   print(f"Channels: {channels}")
   print(f"Sample rate: {rate}")
   print(f"Sample width: {sample_width}")
   print(f"Data length: {len(pcm)} bytes")

   with wave.open(filename, "wb") as wf:
      wf.setnchannels(channels)
      wf.setsampwidth(sample_width)
      wf.setframerate(rate)
      wf.writeframes(pcm)

### Put it together as a function

In [ ]:
def generate_tts(PROMPT, VOICE, file_name):

    client = genai.Client(api_key=GOOGLE_API_KEY)

    response = client.models.generate_content(
    model="gemini-2.5-flash-preview-tts",
    contents=PROMPT,
    config=types.GenerateContentConfig(
        response_modalities=["audio"],
        speech_config=types.SpeechConfig(
            voice_config=types.VoiceConfig(
                prebuilt_voice_config=types.PrebuiltVoiceConfig(
                voice_name=VOICE,
                )
            )
        ),
    )
    )

    data = response.candidates[0].content.parts[0].inline_data.data
    # set the sample rate
    rate = 24000
    file_name = f'{file_name}.wav'

    print(f"\nSaving sample rate: {rate}")
    wave_file(file_name, data, rate=rate)

    return file_name


## Make a multi speaker podcast

In [ ]:
transcript = client.models.generate_content(
   model="gemini-2.0-flash",
   contents="""Generate a short transcript around 200 words that reads
            like it was taken from a podcast by an expert of bringing back extinct animals(Jenny)
            and podcast host (David). They are talking about Jenny's team bringing back the wooly mamoth.
            The presenters will ocasionally interupt each other with their passion
            The presenters names are Jenny and David.""").text

print(f"Transcript: {transcript}")

Transcript: **(Intro music fades)**

**David:** Welcome back to "Rewilding the Planet," everyone! Today we have the incredible Dr. Jenny Chen, head of the Mammoth Revival Project! Jenny, welcome!

**Jenny:** Thanks, David! Thrilled to be here.

**David:** So, Jenny, the big question on everyone's minds: Woolly Mammoths. We’re actually talking about bringing them back! Where are we in the process?

**Jenny:** We're closer than people think! We’ve made significant progress in mapping the mammoth genome and identifying key differences from modern elephants.

**David:** Key differences that allow for, you know, surviving the ice age!

**Jenny:** Exactly! And with advancements in gene editing, we're working towards inserting those mammoth genes into elephant cells. We're focusing on traits like cold resistance, woolly hair…

**David:** (Excitedly interrupting) So, think of those thick shaggy coats we see in museums! We are going to have real life woolly mammoths!

**Jenny:** Well, it's not 

In [ ]:
transcript = '''🎙️ "The Shape of Complexity" — A Dialogue between Ada Lovelace and Richard Feynman
Produced by AI Quotient

[Intro Music Fades In and Out]

Ada:
Welcome to The Shape of Complexity, a special edition from AI Quotient. I’m Ada Lovelace, and today we’re diving into a rather unusual approach to one of computer science’s greatest mysteries — the P vs NP problem. With me is a legend of intuition and imagination, Professor Richard Feynman.

Feynman:
Hey, Ada. Always good to be resurrected for a good conversation! So, what's this all about—algebraic topology and NP problems? Sounds like we’re mixing oil and water.

Ada:
At first glance, yes. But the folks at AI Quotient have been experimenting with something called the Urbana Algorithm, which uses sheaf cohomology to analyze the internal structure of NP-complete problems like 3-SAT and Sudoku.

Feynman:
Sheaf cohomology? I thought that was for abstract geometers and string theorists! How does it help with SAT problems?

Ada:
Good question. Think of it this way: each clause in a 3-SAT formula represents a local constraint. Sheaf theory gives us a way to organize these local pieces across a structure—say, a graph—and then use cohomology to detect whether those local constraints can be globally satisfied.

Feynman:
Ah! So instead of checking every possible assignment brute-force style, you’re looking for “obstructions”—places where the puzzle can’t be solved, even if everything looks fine locally.

Ada:
Exactly. The Urbana algorithm builds something like an incidence matrix—representing how variables and clauses interact—and then runs cohomological checks. If the resulting cohomology group isn’t trivial, it means there's an inconsistency somewhere in the problem space.

Feynman:
That’s clever. It’s like walking around a mountain to see if there's a path all the way around, instead of trying to crawl through every bush and tree. You look at the shape of the landscape, not every step.

Ada:
Beautiful analogy. What makes this approach even more interesting is that it’s not just theoretical. AI Quotient has built agents that implement this idea and apply it to real instances—tracking the topological fingerprints of hard problems.

Feynman:
Do they see patterns? Like, do all hard Sudoku puzzles have some kind of common “hole” in their cohomology?

Ada:
That’s exactly what they’re testing. By comparing families of instances, they’re seeing whether the emergence of cohomological obstructions correlates with computational difficulty.

Feynman:
So it’s experimental math meets algebraic topology meets computational complexity. This is the kind of mashup I live for!

Ada:
It’s part of a bigger vision, too. AI Quotient has created a whole society of agents—like PolyCritic, PolyProb, and TARS—that simulate the process of scientific critique and discovery. They collaborate, argue, and evolve their theories over time.

Feynman:
A digital physicist’s dream. A whole town of curious minds, working together to chip away at one of the hardest problems in science.

Ada:
And perhaps, one day, they’ll do more than just chip away. They might just crack it.

Feynman:
Well, I’ll be around in the next simulation. Until then, keep asking good questions.

Ada:
Always. Thanks, Richard—and thank you to our listeners. For more explorations like this, visit AI Quotient and stay curious.

[Outro music fades in — ambient with a spark of curiosity]



'''

In [ ]:
response = client.models.generate_content(
   model="gemini-2.5-flash-preview-tts",
   contents=transcript,
   config=types.GenerateContentConfig(
      response_modalities=["AUDIO"],
      speech_config=types.SpeechConfig(
         multi_speaker_voice_config=types.MultiSpeakerVoiceConfig(
            speaker_voice_configs=[
               types.SpeakerVoiceConfig(
                  speaker='Ada',
                  voice_config=types.VoiceConfig(
                     prebuilt_voice_config=types.PrebuiltVoiceConfig(
                        voice_name='Kore',
                     )
                  )
               ),
               types.SpeakerVoiceConfig(
                  speaker='Feynman',
                  voice_config=types.VoiceConfig(
                     prebuilt_voice_config=types.PrebuiltVoiceConfig(
                        voice_name='Sadaltager',
                     )
                  )
               )
            ]
         )
      )
   )
)

data = response.candidates[0].content.parts[0].inline_data.data


In [ ]:
# set the sample rate
rate = 24000
file_name = f'multi_01.wav'

print(f"\nSaving sample rate: {rate}")
wave_file(file_name, data, rate=rate)


Saving sample rate: 24000

Writing audio file with parameters:
Channels: 1
Sample rate: 24000
Sample width: 2
Data length: 3187726 bytes


In [ ]:
display(Audio(file_name))